In [1]:
from skimage import io, exposure
from skimage.transform import rotate
import matplotlib.pyplot as plt
import numpy as np

def rescale_intensities(image,flow,fhigh):

    # Scale the intensities for each channel of an R B G image given an upper
    # and lower percentaile and return the re-scaled image.

    red = image[:,:,0]
    green = image[:,:,1]
    blue = image[:,:,2]

    mask = ( red + green + blue ) > 0

    # Pick percentile overwhich to rescale intensities
    #flow = 2
    #fhigh = 98

    plow, phigh = np.percentile(red[mask], (flow, fhigh))
    ls_red_rs= exposure.rescale_intensity(red, in_range=(plow, phigh))

    plow, phigh = np.percentile(green[mask], (flow, fhigh))
    ls_green_rs= exposure.rescale_intensity(green, in_range=(plow, phigh))

    plow, phigh = np.percentile(blue[mask], (flow, fhigh))
    ls_blue_rs= exposure.rescale_intensity(blue, in_range=(plow, phigh))

    # Define empty image
    nx,ny = ls_red_rs.shape
    ls_rgb_stretched = np.zeros([nx,ny,3],dtype=np.float64)

    # set all 3 channels of the image
    ls_rgb_stretched[:,:,0] = ls_red_rs
    ls_rgb_stretched[:,:,1] = ls_green_rs
    ls_rgb_stretched[:,:,2] = ls_blue_rs

    return  ls_rgb_stretched

def prepare_landsat_image(bands):

    # prepare a false color image for a combination of 3 landsat bands
    # Note this is specific to the set of images we provided, and the
    # hardcoded values for rotating need to be changed if you download a new
    # set of landsat images.

    ls_red = io.imread(str(bands[0])+'.tif') # red
    ls_green = io.imread(str(bands[1])+'.tif') # green
    ls_blue = io.imread(str(bands[2])+'.tif') # blue

    ls_red = img_as_float64(ls_red)
    ls_green = img_as_float64(ls_green)
    ls_blue = img_as_float64(ls_blue)

    nx,ny = ls_red.shape
    ls_false = np.zeros([nx,ny,3],dtype=np.float64)

    ls_false[:,:,0] = ls_red
    ls_false[:,:,1] = ls_green
    ls_false[:,:,2] = ls_blue

    flow = 42
    fhigh = 90

    ls_false_rescale = rescale_intensities(ls_false,flow,fhigh)

    return ls_false_rescale

def PrintArrayInfo(a):
    print("Array info:")
    print("shape:", a.shape)
    print("dtype:", a.dtype)
    print("min, max:", a.min(), a.max())

from skimage import img_as_ubyte, img_as_uint, img_as_float64
from PIL import Image

In [2]:
%matplotlib osx

from PIL import ImageChops
import matplotlib.animation as animation

def get_image(bands):
    ls_false = prepare_landsat_image(bands)
    N = 7
    imageRGB = Image.fromarray(img_as_ubyte(ls_false))
    imageIndexed = imageRGB.quantize(colors=N, kmeans=1)
    im = imageIndexed.convert("RGB")
    return im

bands_list = [
    [
        "HLS.L30.T11SLT.2020281T182839.v2.0.B04",
        "HLS.L30.T11SLT.2020281T182839.v2.0.B03",
        "HLS.L30.T11SLT.2020281T182839.v2.0.B02"
    ],
    [
        "HLS.L30.T11SLT.2021283T182844.v2.0.B04",
        "HLS.L30.T11SLT.2021283T182844.v2.0.B03",
        "HLS.L30.T11SLT.2021283T182844.v2.0.B02" 
    ],
    [
        "HLS.L30.T11SLT.2022302T182858.v2.0.B04",
        "HLS.L30.T11SLT.2022302T182858.v2.0.B03",
        "HLS.L30.T11SLT.2022302T182858.v2.0.B02"
    ],
    [
        "HLS.L30.T11SLT.2023329T182838.v2.0.B04",
        "HLS.L30.T11SLT.2023329T182838.v2.0.B03",
        "HLS.L30.T11SLT.2023329T182838.v2.0.B02"
    ]
]

print('Getting images')
images = [get_image(bands) for bands in bands_list]

fig = plt.figure()
nFrames = 100

print('Starting animation')

frames = []
image = images[0]
for j in range(len(images) - 1):
    diff = ImageChops.subtract(images[j+1], images[j])

    for i in range(nFrames):
        image = ImageChops.add(image, diff.point(lambda k: k / nFrames))
        frames.append([plt.imshow(image)])

ani = animation.ArtistAnimation(fig, frames, interval=10, blit=True, repeat=False)
ani.save("test.mp4")
plt.show()

Getting images
Starting animation


2023-11-28 04:36:47.064 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:36:47.402 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:36:47.755 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:36:48.098 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:36:48.436 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:36:48.776 python[57279:119

2023-11-28 04:37:01.634 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:01.961 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:02.304 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:02.640 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:02.981 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:03.322 python[57279:119

2023-11-28 04:37:16.443 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:16.795 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:17.145 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:17.554 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:17.899 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:18.239 python[57279:119

2023-11-28 04:37:31.318 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:31.661 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:32.000 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:32.337 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:32.674 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:37:33.019 python[57279:119

...

2023-11-28 04:38:37.719 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:37.733 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:37.747 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:37.761 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:37.777 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:37.793 python[57279:119

2023-11-28 04:38:38.565 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:38.579 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:38.594 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:38.609 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:38.624 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:38.639 python[57279:119

2023-11-28 04:38:39.401 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:39.415 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:39.431 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:39.446 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:39.461 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:39.476 python[57279:119

2023-11-28 04:38:40.233 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:40.248 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:40.263 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:40.278 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:40.293 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
2023-11-28 04:38:40.308 python[57279:119

2023-11-28 04:38:41.073 python[57279:11968872] *** Assertion failure in +[NSEvent otherEventWithType:location:modifierFlags:timestamp:windowNumber:context:subtype:data1:data2:], NSEvent.m:737
Traceback (most recent call last):
  File "/Users/spiderfencer/miniconda3/lib/python3.10/site-packages/tornado/ioloop.py", line 738, in _run_callback
    ret = callback()
  File "/Users/spiderfencer/miniconda3/lib/python3.10/site-packages/ipykernel/kernelbase.py", line 461, in advance_eventloop
    eventloop(self)
  File "/Users/spiderfencer/miniconda3/lib/python3.10/site-packages/ipykernel/eventloops.py", line 353, in loop_cocoa
    if kernel.shell_stream.flush(limit=1):
  File "/Users/spiderfencer/miniconda3/lib/python3.10/site-packages/zmq/eventloop/zmqstream.py", line 503, in flush
    self._rebuild_io_state()
  File "/Users/spiderfencer/miniconda3/lib/python3.10/site-packages/zmq/eventloop/zmqstream.py", line 641, in _rebuild_io_state
    self._update_handler(state)
  File "/Users/spiderfence